## SetUp Parameters

In [40]:
utilities_path = '../utilities/'
model_path = '../models/'
data_path = '../data/'
results_path = '../results/'

In [7]:
from datetime import datetime
# datetime object containing current date and time
now = datetime.now()
dt_string = now.strftime("%d-%m-%Y")
dt_string = "13-05-2020"
global_path = "../models/"
model_path = ".model"
txt_extension = ".txt"
path_ft =  global_path + "ft_"+ dt_string + txt_extension
path_w2v =  global_path + "w2v_"+ dt_string + model_path
path_glove = global_path + "gloVe_"+ dt_string + txt_extension

### Import Models

In [8]:
from gensim.test.utils import common_texts, get_tmpfile,datapath
from gensim.scripts.glove2word2vec import glove2word2vec
from gensim.models import KeyedVectors
model_ft = KeyedVectors.load_word2vec_format(path_ft)

In [9]:
from gensim.test.utils import common_texts, get_tmpfile,datapath
from gensim.models import Word2Vec
path = get_tmpfile(path_w2v)
model_w2v = Word2Vec.load(path_w2v)
model_w2v = model_w2v.wv

In [10]:
from gensim.test.utils import common_texts, get_tmpfile,datapath
from gensim.scripts.glove2word2vec import glove2word2vec
from gensim.models import KeyedVectors
model_glove = KeyedVectors.load_word2vec_format(path_glove)

In [11]:
model_glove.vocab

{'de': <gensim.models.keyedvectors.Vocab at 0x7f09cf32feb0>,
 'la': <gensim.models.keyedvectors.Vocab at 0x7f09cf32f640>,
 'et': <gensim.models.keyedvectors.Vocab at 0x7f09cf32fe20>,
 'à': <gensim.models.keyedvectors.Vocab at 0x7f09cf32fe50>,
 'le': <gensim.models.keyedvectors.Vocab at 0x7f09cf32f940>,
 'en': <gensim.models.keyedvectors.Vocab at 0x7f09cf32ffd0>,
 'les': <gensim.models.keyedvectors.Vocab at 0x7f09cf32ff40>,
 'des': <gensim.models.keyedvectors.Vocab at 0x7f09cf32ff70>,
 'du': <gensim.models.keyedvectors.Vocab at 0x7f09cf32f880>,
 'pour': <gensim.models.keyedvectors.Vocab at 0x7f09cf32f550>,
 'sur': <gensim.models.keyedvectors.Vocab at 0x7f09cf32f580>,
 'par': <gensim.models.keyedvectors.Vocab at 0x7f09cf32f4f0>,
 'un': <gensim.models.keyedvectors.Vocab at 0x7f09cf32f520>,
 'une': <gensim.models.keyedvectors.Vocab at 0x7f09cf32f490>,
 'au': <gensim.models.keyedvectors.Vocab at 0x7f09cf32f4c0>,
 'a': <gensim.models.keyedvectors.Vocab at 0x7f09cf32f430>,
 'dans': <gensim.mo

### Import DataSet

In [12]:
import pandas as pd 
df = pd.read_csv('../data/eval.csv')

In [13]:
#df = (df[(df['legal_name'] == "THERADIAG SA")])
#df=df.sample(10)

In [14]:
df

Unnamed: 0      siren legal_name     id  \
0               1  419838529      IPSEN   2894   
1               2  419838529      IPSEN   3057   
2               5  419838529      IPSEN   7375   
3               7  419838529      IPSEN  10659   
4               8  419838529      IPSEN  12797   
...           ...        ...        ...    ...   
19290       56749  337080089        FCN  52705   
19291       56750  337080089        FCN  53160   
19292       56751  337080089        FCN  56724   
19293       56752  337080089        FCN  57545   
19294       56753  337080089        FCN  58607   

                                             url_article  \
0      http://www.boursier.com/actions/actualites/new...   
1      http://www.boursier.com/actions/actualites/new...   
2      http://www.boursier.com/actions/actualites/new...   
3      http://www.latribune.fr/entreprises-finance/in...   
4      http://www.boursier.com/actions/actualites/new...   
...                                                  ...   
19290  https://www.fcn.fr/Page/Juriste-Junior-Droit-S...   
19291  https://twitter.com/CabinetFCN/status/10571748...   
19292  https://www.fcn.fr/Page/Secretaire-comptable--...   
19293  https://www.fcn.fr/Page/Collaborateur-comptabl...   
19294  https://www.fcn.fr/Page/Secretaire-juridique--...   

                                                  corpus  
0      ipsen : accord important avec probi publié le ...  
1      la médecine générale d'ipsen en panne au er tr...  
2      ipsen : david meek rejoint le groupe en qualit...  
3      le français ipsen ne veut pas rater le train d...  
4      ipsen affiche une croissance des ventes de ,% ...  
...                                                  ...  
19290  cette page n'existe plus sur le site - groupe ...  
19291  cabinet fcn sur twitter : "#fcn #comptable #re...  
19292  cette page n'existe plus sur le site - groupe ...  
19293  cette page n'existe plus sur le site - groupe ...  
19294  cette page n'existe plus sur le site - groupe ...  

[19295 rows x 6 columns]

In [15]:
# Add columns to store results

df['eval_set_w2v'] = ""
df['eval_set_ft'] = ""
df['eval_set_glove'] = ""
df['eval_number_w2v'] = ""
df['eval_number_ft'] = ""
df['eval_number_glove'] = ""
df['corpus'] = df['corpus'].apply(lambda corpus: set(corpus.split(" ")))

In [16]:
# Get name of all companies in eval dataset 
vocab = set(df.legal_name)

In [17]:
# Map SIREN to legal name and vice versa
from collections import defaultdict
siren_to_legal_name = defaultdict(str)
legal_n_to_siren = defaultdict(str)
for i,row in df.iterrows():
    siren_to_legal_name[row.siren] = row.legal_name
    legal_n_to_siren[row.legal_name] = row.siren

### Create Result Dictionnary

In [18]:
import pickle
# Load common names dictionnary
file = open('../utilities/legal_to_common_names.obj', 'rb') 
legal_to_common_name = pickle.load(file)


In [19]:
def add_eval_set(dataframe, legal_name, nearest_words,method):
    occurences_word = defaultdict(int)
    df_legal_name = dataframe[(dataframe['legal_name'] == legal_name)]
    for i,row in df_legal_name.iterrows():
        nearest_words_set = set(nearest_words)
        corpus_set = row.corpus
        inters_ = nearest_words_set.intersection(corpus_set)
        if(method == 'w2v'):
            df['eval_set_w2v'][i] =  list(inters_)
            df['eval_number_w2v'][i] = len(inters_)
        elif(method == 'ft'):
            df['eval_set_ft'][i] =  list(inters_)
            df['eval_number_ft'][i] = len(inters_)
        else:
            df['eval_set_glove'][i] =  list(inters_)
            df['eval_number_glove'][i] = len(inters_)
        for word in inters_:
                occurences_word[word] +=1
    return occurences_word

In [20]:
def create_emb_dict(word):
    emb_dict = defaultdict(list)
    emb_dict['ft'] = get_most_similar(word,model_ft)
    emb_dict['w2v'] = get_most_similar(word,model_w2v)
    emb_dict['glove'] = get_most_similar(word,model_glove)
    return emb_dict

In [21]:
def get_nearest_ft(word):
    nearest_words  = model_ft.get_nearest_neighbors(word.lower(),10)
    return [[(y),round(x,2)] for x,y in nearest_words]

In [22]:
import numpy as np
def get_composed_word_vector(composed_word,wordVectors): 
    res = []
    for word in composed_word.split():
        if(word.lower() in wordVectors.vocab):
            res.append(wordVectors[word.lower()])
    if(len(res)==0):
        return res 
    return np.mean(res,axis=0)

In [23]:
def get_most_similar(word,model,topn=10):
    res = []
    if(len(word.split(" ")) > 0):
        vector = get_composed_word_vector(word,model_glove)
    else: 
        vector = model[word.lower()]
    if(len(vector)>0):
        nearest_words = model.most_similar([vector], topn=topn)
        res =  [[(x),round(y,2)] for x,y in nearest_words]
    return res

In [24]:
def score2(legal_name,word_occurences):
    return round((word_occurences / len(df[(df['legal_name'] == legal_name)])),4)
               

In [25]:
def all_indices(value, qlist):
    indices = []
    idx = -1
    while True:
        try:
            idx = qlist.index(value, idx+1)
            indices.append(idx)
        except ValueError:
            break
    return indices

In [26]:
def compute_score2(dataframe,nearest_words, legal_name,method):
    occurences_words = add_eval_set(df, legal_name,[x[0] for x in nearest_words],method)
    for word in nearest_words: 
        word.append(score2(legal_name, occurences_words[word[0]]))

In [27]:
def get_nearest_from_dict(dict_,legal_name,method):
    res = []
    common_names_dict = dict_[legal_name] 
    for common_name in common_names_dict.keys():
        #print(dict_[legal_name][common_name])
        res.append(dict_[legal_name][common_name][method])
    return [y for x in res for y in x]

In [28]:
def getTime(start,end):
    hours, rem = divmod(end-start, 3600)
    minutes, seconds = divmod(rem, 60)
    time_since_start = "Time:  {:0>2}:{:0>2}:{:05.2f}".format(int(hours),int(minutes),seconds)
    return time_since_start

In [29]:
def fusion(nearest_words):
    word_list = [x[0] for x in nearest_words]
    res = []
    list_of_pairs = []
    for i,word in enumerate(word_list):
        indices_word = all_indices(word,word_list)
        list_of_pairs.append(indices_word)
    list_of_pairs = [list(item) for item in set(tuple(row) for row in list_of_pairs)]
    for pairs in list_of_pairs:
        if(len(pairs)>1):
            res.append(fusion_list([x for j,x in enumerate(nearest_words) if j in pairs ]))
        else: 
            res.append(nearest_words[pairs[0]])
    return res
    

In [30]:
def fusion_list(l):
    new_similarity = round(sum([x[1] for x in l]),3)
    return [l[0][0], new_similarity, l[0][2]]

In [31]:
import time
nearest = defaultdict(dict)
new_nearest = defaultdict(dict)
methods = ['ft','w2v','glove']
# Create dictionnary with nearest vectors
percent = 0
start = time.time()
for i,legal_name in enumerate(vocab): 
    # Logging
    if(i % 150 == 0):
        time_ = getTime(start,time.time())
        print("0%" + "=" *(int(percent/10))+ str(percent) +"%, " + time_, end="\r" )
        percent +=10
    legal_name_dict = defaultdict(dict)
    nearest[legal_name] = legal_name_dict
    siren = legal_n_to_siren[legal_name]
    if(siren in legal_to_common_name.keys()):
        common_names = legal_to_common_name[siren]
        # For each common name compute nearest words per embedding technique 
        for common_n in common_names:
            legal_name_dict[common_n] = create_emb_dict(common_n)     
    else:
        legal_name_dict[legal_name] = emb_dict
    legal_name_dict = defaultdict(list)
    new_nearest[legal_name] = legal_name_dict
    for method in methods:
        fusioned_dict = defaultdict(list)
        # Compute score2
        compute_score2(df,get_nearest_from_dict(nearest,legal_name,method),legal_name,method)
        # Fusion result of each common name
        nearest_fusioned = fusion(get_nearest_from_dict(nearest,legal_name,method))
        #nearest_fusioned
        legal_name_dict[method] = nearest_fusioned
        # Compute Gobal Score to evaluate method
        sgx1 = round(sum(x[1] for x in nearest_fusioned),3)
        sgx2 = round(sum(x[2]for x in nearest_fusioned),3)
        sgx3 = sgx1*sgx2
        scores = [('sgx1',sgx1),('sgx2',sgx2),('sgx3',sgx3)]
        legal_name_dict[method].insert(0,scores)

<ipython-input-19-520e0068ad97>:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['eval_set_ft'][i] =  list(inters_)
<ipython-input-19-520e0068ad97>:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['eval_number_ft'][i] = len(inters_)
<ipython-input-19-520e0068ad97>:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['eval_set_w2v'][i] =  list(inters_)
<ipython-input-19-520e0068ad97>:10: SettingWithCopyWarning: 
A value is trying

In [33]:
new_nearest

defaultdict(dict,
            {'HIOLLE INDUSTRIES': defaultdict(list,
                         {'ft': [[('sgx1', 4.25),
                            ('sgx2', 0.0),
                            ('sgx3', 0.0)],
                           ['dev', 0.21, 0.0],
                           ['dadmission', 0.2, 0.0],
                           ['évolue', 0.23, 0.0],
                           ['dhorizontal', 0.49, 0.0],
                           ['pfeiffer', 0.21, 0.0],
                           ['évoluer', 0.2, 0.0],
                           ['cs', 0.2, 0.0],
                           ['etp', 0.21, 0.0],
                           ['quau', 0.2, 0.0],
                           ['évolué', 0.43, 0.0],
                           ['“je', 0.41, 0.0],
                           ['dincidence', 0.2, 0.0],
                           ['ateme', 0.21, 0.0],
                           ['dimerys', 0.2, 0.0],
                           ['dois', 0.2, 0.0],
                           ['horizontal', 0.45, 0.0

In [34]:
df.sample(20)

Unnamed: 0      siren  \
487           558  652014051   
13489       16724  473801330   
14482       18453  808234801   
237           269  542107651   
1630         1922  542005376   
4545         5435  331518498   
18978       40641  327733432   
13262       16373  394149496   
12170       14858  326966777   
13404       16600  434317293   
11359       13684  662001403   
3946         4718  403561137   
14240       18006  389522152   
17972       30502  353150261   
11124       13351  352980601   
12032       14660  343115135   
7684         9159  390406320   
17758       29557  803980218   
6231         7380  329211734   
13405       16601  434317293   

                                              legal_name     id  \
487                                            CARREFOUR  26977   
13489                  UNION FINANCIERE DE FRANCE BANQUE  60736   
14482                                MONDELEZ FRANCE SAS   4642   
237                                                ENGIE  54816   
1630                                            FAURECIA   8215   
4545                                            SA ESKER  10052   
18978                                             ISAGRI  43131   
13262                                             PARROT   9471   
12170                                           ECONOCOM  31202   
13404                                    VENTE PRIVEECOM  28291   
11359                          GAZTRANSPORT ET TECHNIGAZ  26495   
3946                              PHARMAGEST INTERACTIVE  29685   
14240                          GROUPAMA ASSET MANAGEMENT  72022   
17972                                       MODIS FRANCE  73605   
11124                                       DERICHEBOURG  35372   
12032  CAISSE NATIONALE DE REASSURANCE MUTUELLE AGRIC...  13080   
7684                                        CATANA GROUP  66017   
17758                                     GROUPE MIIMOSA  47048   
6231                     SOCIETE D'EDITION DE CANAL PLUS  44576   
13405                                    VENTE PRIVEECOM  30472   

                                             url_article  \
487    http://www.brefeco.com/actualite/logistique-tr...   
13489  http://www.boursier.com/actions/actualites/new...   
14482  http://www.lesechos.fr/industrie-services/cons...   
237    http://www.petrole-et-gaz.fr/engie-gary-leibow...   
1630   https://www.abcbourse.com/marches/faurecia-a-r...   
4545   http://www.boursier.com/actions/actualites/new...   
18978  https://www.distributique.com/actualites/lire-...   
13262  http://www.journaldunet.com/economie/industrie...   
12170  http://www.distributique.com/actualites/lire-e...   
13404  http://www.boursier.com/actions/actualites/new...   
11359  http://www.boursier.com/actions/actualites/new...   
3946   http://www.boursier.com/actions/actualites/new...   
14240  https://offres.groupama-gan-recrute.com/offre-...   
17972  https://twitter.com/ModisRecruteFR/status/1173...   
11124  http://www.fusacq.com/buzz/derichebourg-prepar...   
12032  http://rss.argusdelassurance.com/~r/argusdelas...   
7684   http://www.boursedirect.fr/fr/actualites/categ...   
17758  http://feedproxy.google.com/~r/Maddyness/~3/GC...   
6231   http://www.cbnews.fr/mouvements/christine-cauq...   
13405  http://rss.lsa-conso.fr/~r/Lsa-rss/~3/sFdB3gXQ...   

                                                  corpus  \
487    {produits, filiale, se, française, jours, serv...   
13489  {dédiée, depuis, annonce, l'activité, autorisé...   
14482  {restructurer, se, engagé, cession, europe,, p...   
237    {, merrill, image, stratégies, directeur, engi...   
1630   {hausse, une, ses, nouvelle, vos, ,e., peugeot...   
4545   {nos, autorisé, chiffre, d'esker, publications...   
18978  {comptable, ils, depuis, challenge, l'activité...   
13262  {, disposer, ils, moment, appareil, souscrites...   
12170  {ils, depuis, menait, directeur, qu'une, franc...   
13404  {ouvre, domaine, nos, autorisé, publications.\...   
11359

In [33]:
df.to_csv('results' + dt_string + '.csv')

In [35]:
ftEval = df['eval_number_ft'].mean()
w2vEval = df['eval_number_w2v'].mean()
gloveEval = df['eval_number_glove'].mean()
print(ftEval)
print(w2vEval)
print(gloveEval)

0.05586939621663643
0.3023581238662866
2.002487691111687


In [37]:
import json
import codecs

with codecs.open('results-with-fusion.json', 'w',encoding='utf-8') as fp:
    json.dump(nearest,fp,ensure_ascii=False)

### Prediction 

In [41]:
# DataSetPath 
prediction_path = utilities_path + 'groupC_scrap.obj'


In [42]:
file = open(prediction_path, 'rb') 
df_prediction = pickle.load(file)

In [43]:
df_prediction

[{'url_article': 'http://www.touleco.fr/Toulouse-Cerenis-Therapeutics-recherche-partenaire-particulier,19590',
  'siren': '481637718',
  'corpus': '\n'},
 {'url_article': 'http://www.boursier.com/actions/actualites/news/cerenis-va-lever-960-ke-a-0-32-euro-l-action-798116.html?rss',
  'siren': '481637718',
  'corpus': "Cerenis va lever 960 kE à 0,32 euro l'action\n"},
 {'url_article': 'http://www.businesswire.fr/news/fr/20170217005562/fr/?feedref=JjAwJuNHiystnCoBq_hl-YorNIXXeJUidDamMzBr2lWidyPM7v09-Iu6pzb4ljfxrCOi9QzgjCezTS3Nw_X6kJUrpSBm-Hav1w-UkdSlG3lZPJbLme68RX7HACdBAEYGuY882fGf0lt1RTkSC2Xm4A==',
  'siren': '481637718',
  'corpus': 'CERENIS THERAPEUTICS : RÉSULTATS ANNUELS 2016 | Business Wire\n'},
 {'url_article': 'http://www.businesswire.fr/news/fr/20171107006957/fr/?feedref=JjAwJuNHiystnCoBq_hl-YorNIXXeJUidDamMzBr2lWidyPM7v09-Iu6pzb4ljfxrCOi9QzgjCezTS3Nw_X6kJUrpSBm-Hav1w-UkdSlG3lZPJbLme68RX7HACdBAEYGuY882fGf0lt1RTkSC2Xm4A==',
  'siren': '481637718',
  'corpus': '\n'},
 {'url_articl